In [1]:
# Collaborative Filtering : User similarity based recommendation
## 1) Get similarities of between all users (using Similarity measures)
## 2) Get similarities between current user and others
## 3) Get estimated rating of items which current user do not rate yet
## 4) Recommend N items ranked high

# Similarity measure
# 1) Correlations
# 2) Cosine similarity : simil(x,y) = /sum_i{r_{x,i}*r_{y,i}}/(/sqrt{/sum_i{r_{x,i}**2}}*/sqrt{/sum_i{r_{y,i}**2}})
# 3) Tanimoto coefficient (Binary data) : simil(x,y) = c/(a+b-c) 
# 4) Jaccard coefficeint (Binary data)
# 5) Pearson correlation coefficient

In [2]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.model_selection import train_test_split
import pandas as pd
import numpy as np

In [3]:
# data directory absolute path
data_dir = '../../../../data/'

# Read data
u_cols = ['user_id', 'age', 'sex', 'occupation', 'zip_code']
users = pd.read_csv(data_dir+'u.user', sep='|', names=u_cols, encoding='latin-1')

i_cols = ['movie_id', 'title', 'release date', 'video release date', 'IMDB URL', 
          'unknown', 'Action', 'Adventure', 'Animation', 'Childeren\'s', 'Comedy', 'Crime', 'Documentary', 'Drama',
          'Fantasy', 'Film-Noir', 'Horror', 'Musical', 'Mystery', 'Romance', 'Sci-Fi', 'Thriller', 'War', 'Western'
         ]
movies = pd.read_csv(data_dir+'u.item', sep='|', names=i_cols, encoding='latin-1')

r_cols = ['user_id', 'movie_id', 'rating', 'timestamp']
ratings = pd.read_csv(data_dir+'u.data', sep='\t', names=r_cols, encoding='latin-1')

# timestamp 제거 
ratings = ratings.drop('timestamp', axis=1)
# movie ID와 title 빼고 다른 데이터 제거
movies = movies[['movie_id', 'title']]

### User-Item Matrix

In [8]:
x = ratings.copy()
y = ratings['user_id']
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.25, stratify=y)

def RMSE(y_true, y_pred):
    return np.sqrt(np.mean((np.array(y_true) - np.array(y_pred))**2))

def score(model):
    id_pairs = zip(x_test['user_id'], x_test['movie_id'])
    y_pred = np.array([model(user, movie) for (user, movie) in id_pairs])
    y_true = np.array(x_test['rating'])
    return RMSE(y_true, y_pred)

rating_matrix = x_train.pivot(index='user_id', columns='movie_id', values='rating')
# print(x_train)
# print(rating_matrix)

       user_id  movie_id  rating
14665       70       185       4
7371       114       183       5
57399      749       168       5
73783      804       123       4
66163      747       651       5
...        ...       ...     ...
82539      868       237       1
68302       79       515       5
66820      878       137       3
1430       216       196       5
37799      262        95       3

[75000 rows x 3 columns]
movie_id  1     2     3     4     5     6     7     8     9     10    ...  \
user_id                                                               ...   
1          5.0   3.0   4.0   3.0   NaN   5.0   4.0   NaN   5.0   3.0  ...   
2          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   2.0  ...   
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
5          4.0   3.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
...        ...   ...   ...   ...   ... 

### User-User Similarity Matrix 

In [5]:
# get cosine similarities of all user in train set
dummy_matrix = rating_matrix.copy().fillna(0)
user_similarity = cosine_similarity(dummy_matrix, dummy_matrix)
user_similarity = pd.DataFrame(user_similarity, index=rating_matrix.index, columns=rating_matrix.index)
print('User similirarity matrix')
user_similarity

User similirarity matrix


user_id       1         2         3         4         5         6         7    \
user_id                                                                         
1        1.000000  0.150513  0.037295  0.048151  0.263383  0.349264  0.326403   
2        0.150513  1.000000  0.129142  0.148482  0.016750  0.225843  0.099963   
3        0.037295  0.129142  1.000000  0.269551  0.027366  0.033036  0.045695   
4        0.048151  0.148482  0.269551  1.000000  0.012979  0.057282  0.091805   
5        0.263383  0.016750  0.027366  0.012979  1.000000  0.167054  0.305592   
...           ...       ...       ...       ...       ...       ...       ...   
939      0.063777  0.216210  0.034604  0.040523  0.041142  0.102535  0.066013   
940      0.217761  0.176406  0.095944  0.184298  0.214432  0.286939  0.286422   
941      0.119824  0.187412  0.111628  0.143794  0.074653  0.127912  0.069251   
942      0.130998  0.119281  0.109879  0.145540  0.139022  0.267901  0.220112   
943      0.286845  0.043539  0.019794  0.036509  0.260785  0.171146  0.280098   

user_id       8         9         10   ...       934       935       936  \
user_id                                ...                                 
1        0.285906  0.045740  0.301749  ...  0.256743  0.065118  0.208456   
2        0.080489  0.151451  0.136857  ...  0.108122  0.233757  0.289701   
3        0.065036  0.055763  0.020213  ...  0.009422  0.018802  0.108007   
4        0.129024  0.000000  0.054323  ...  0.014895  0.049541  0.084371   
5        0.203652  0.073092  0.164914  ...  0.294876  0.069159  0.055746   
...           ...       ...       ...  ...       ...       ...       ...   
939      0.093459  0.052395  0.076728  ...  0.061968  0.279135  0.255024   
940      0.215273  0.086037  0.254996  ...  0.215199  0.066838  0.185291   
941      0.169295  0.084509  0.093123  ...  0.037124  0.042743  0.135570   
942      0.135485  0.058274  0.139647  ...  0.137432  0.049123  0.066395   
943      0.252601  0.037763  0.202882  ...  0.169765  0.119374  0.117400   

user_id       937       938       939       940       941       942       943  
user_id                                                                        
1        0.119826  0.084122  0.063777  0.217761  0.119824  0.130998  0.286845  
2        0.300139  0.258681  0.216210  0.176406  0.187412  0.119281  0.043539  
3        0.053014  0.025639  0.034604  0.095944  0.111628  0.109879  0.019794  
4        0.125716  0.072622  0.040523  0.184298  0.143794  0.145540  0.036509  
5        0.005673  0.079731  0.041142  0.214432  0.074653  0.139022  0.260785  
...           ...       ...       ...       ...       ...       ...       ...  
939      0.153422  0.284269  1.000000  0.069793  0.179472  0.034600  0.127403  
940      0.150762  0.118289  0.069793  1.000000  0.129456  0.244374  0.235048  
941      0.144618  0.254508  0.179472  0.129456  1.000000  0.028804  0.077996  
942      0.086180  0.051169  0.034600  0.244374  0.028804  1.000000  0.124978  
943      0.021798  0.131774  0.127403  0.235048  0.077996  0.124978  1.000000  

[943 rows x 943 columns]

In [9]:
def simple_cf(user_id, movie_id):
    if movie_id in rating_matrix:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_matrix[movie_id].copy() # get rating from user-item matrix
        print(user_id, movie_id)
        print(movie_ratings)
        none_rating_idx = movie_ratings[movie_ratings.isnull()].index # list
        movie_ratings = movie_ratings.dropna()
        sim_scores = sim_scores.drop(none_rating_idx)
        mean_rating = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
    else:
        mean_rating = 3.0
    
    return mean_rating

score(simple_cf)

221 288
user_id
1      NaN
2      3.0
3      2.0
4      4.0
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 288, Length: 943, dtype: float64
102 411
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 411, Length: 943, dtype: float64
269 441
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      1.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 441, Length: 943, dtype: float64
455 511
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    4.0
943    NaN
Name: 511, Length: 943, dtype: float64
880 879
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    4.0
943    NaN
Name: 879, Length: 943, dtype: float64
472 94
user_id
1      2.0
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943   

913 302
user_id
1      NaN
2      5.0
3      2.0
4      NaN
5      NaN
      ... 
939    NaN
940    4.0
941    NaN
942    NaN
943    NaN
Name: 302, Length: 943, dtype: float64
742 258
user_id
1      5.0
2      3.0
3      2.0
4      5.0
5      NaN
      ... 
939    4.0
940    5.0
941    4.0
942    4.0
943    NaN
Name: 258, Length: 943, dtype: float64
399 697
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 697, Length: 943, dtype: float64
484 141
user_id
1      3.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 141, Length: 943, dtype: float64
339 503
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 503, Length: 943, dtype: float64
747 580
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 580, Lengt

61 342
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 342, Length: 943, dtype: float64
561 182
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    5.0
Name: 182, Length: 943, dtype: float64
387 47
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 47, Length: 943, dtype: float64
79 1008
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 1008, Length: 943, dtype: float64
566 137
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    3.0
941    NaN
942    NaN
943    NaN
Name: 137, Length: 943, dtype: float64
798 259
user_id
1      1.0
2      NaN
3      NaN
4      NaN
5      1.0
      ... 
939    NaN
940    4.0
941    NaN
942    4.0
943    NaN
Name: 2

554 56
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    5.0
941    NaN
942    NaN
943    5.0
Name: 56, Length: 943, dtype: float64
864 541
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    4.0
Name: 541, Length: 943, dtype: float64
487 98
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 98, Length: 943, dtype: float64
203 150
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    3.0
941    NaN
942    NaN
943    NaN
Name: 150, Length: 943, dtype: float64
99 338
user_id
1      NaN
2      NaN
3      2.0
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 338, Length: 943, dtype: float64
371 194
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      4.0
      ... 
939    NaN
940    5.0
941    NaN
942    NaN

7 419
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    2.0
Name: 419, Length: 943, dtype: float64
514 136
user_id
1      3.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 136, Length: 943, dtype: float64
893 125
user_id
1      3.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 125, Length: 943, dtype: float64
82 895
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 895, Length: 943, dtype: float64
354 753
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 753, Length: 943, dtype: float64
622 174
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      5.0
      ... 
939    NaN
940    4.0
941    NaN
942    NaN
943    4.0
Name: 17

...

417 792
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 792, Length: 943, dtype: float64
645 963
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 963, Length: 943, dtype: float64
44 132
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 132, Length: 943, dtype: float64
286 234
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    4.0
943    3.0
Name: 234, Length: 943, dtype: float64
894 10
user_id
1      3.0
2      2.0
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 10, Length: 943, dtype: float64
24 58
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    4.0
Name: 58, 

648 633
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 633, Length: 943, dtype: float64
504 168
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    2.0
Name: 168, Length: 943, dtype: float64
453 402
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      1.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    2.0
Name: 402, Length: 943, dtype: float64
399 426
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    4.0
Name: 426, Length: 943, dtype: float64
23 14
user_id
1      5.0
2      4.0
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    3.0
941    NaN
942    NaN
943    NaN
Name: 14, Length: 943, dtype: float64
12 174
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      5.0
      ... 
939    NaN
940    4.0
941    NaN
942    NaN
943    4.

279 515
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 515, Length: 943, dtype: float64
846 230
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    1.0
Name: 230, Length: 943, dtype: float64
429 491
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 491, Length: 943, dtype: float64
373 15
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    5.0
940    NaN
941    NaN
942    NaN
943    NaN
Name: 15, Length: 943, dtype: float64
293 616
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 616, Length: 943, dtype: float64
63 116
user_id
1      3.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    2.0
941    NaN
942    NaN
943    NaN
Name: 116, Length: 

280 416
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      1.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 416, Length: 943, dtype: float64
246 719
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 719, Length: 943, dtype: float64
823 655
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    4.0
Name: 655, Length: 943, dtype: float64
113 329
user_id
1      NaN
2      NaN
3      4.0
4      5.0
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 329, Length: 943, dtype: float64


1.0163707888817692

In [ ]:
# practice 3-1 : using Pearson correlation coefficient

### Neighbor method

In [10]:
# RMSE with neighbor
def score(model, neighbor_size=0):
    id_pairs = zip(x_test['user_id'], x_test['movie_id'])
    y_pred = np.array([model(user, movie, neighbor_size) for (user, movie) in id_pairs])
    y_true = np.array(x_test['rating'])
    return RMSE(y_true, y_pred)

In [11]:
# getting prediction with fixed neightbor size
def cf_knn(user_id, movie_id, neighbor_size=0):
    if movie_id in rating_matrix:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_matrix[movie_id].copy() # get rating from user-item matrix
        none_rating_idx = movie_ratings[movie_ratings.isnull()].index # list
        movie_ratings = movie_ratings.drop(none_rating_idx)
        sim_scores = sim_scores.drop(none_rating_idx)
        
        # if neighbor size is not fixed
        if neighbor_size == 0:
            mean_rating = np.dot(sim_scores, movie_ratings) / sim_scores.sum() # weighted average
        
        # if neighbor size is fixed
        else:
            if len(sim_scores) > 1:
                neighbor_size = min(neighbor_size, len(sim_scores))
                sim_scores = np.array(sim_scores)
                movie_ratings = np.array(movie_ratings)
                
                user_idx = np.argsort(sim_scores)
                sim_scores = sim_scores[user_idx][-neighbor_size:]
                movie_ratings = movie_ratings[user_idx][-neighbor_size:]
                mean_rating = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
            else:
                mean_rating = 3.0
        
    else:
        mean_rating = 3.0
    
    return mean_rating

score(cf_knn, neighbor_size=30)            

1.005266588311199

In [16]:
# Get full matrix and cosine similarity
rating_matrix = ratings.pivot_table(values='rating', index='user_id', columns='movie_id')
rating_matrix

movie_id  1     2     3     4     5     6     7     8     9     10    ...  \
user_id                                                               ...   
1          5.0   3.0   4.0   3.0   3.0   5.0   4.0   1.0   5.0   3.0  ...   
2          4.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   2.0  ...   
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
5          4.0   3.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   5.0   NaN  ...   
940        NaN   NaN   NaN   2.0   NaN   NaN   4.0   5.0   3.0   NaN  ...   
941        5.0   NaN   NaN   NaN   NaN   NaN   4.0   NaN   NaN   NaN  ...   
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
943        NaN   5.0   NaN   NaN   NaN   NaN   NaN   NaN   3.0   NaN  ...   

movie_id  1673  1674  1675  1676  1677  1678  1679  1680  1681  1682  
user_id                                                               
1          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
5          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
940        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
941        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
943        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[943 rows x 1682 columns]

In [17]:
dummy_matrix = rating_matrix.copy().fillna(0)
dummy_matrix

movie_id  1     2     3     4     5     6     7     8     9     10    ...  \
user_id                                                               ...   
1          5.0   3.0   4.0   3.0   3.0   5.0   4.0   1.0   5.0   3.0  ...   
2          4.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   2.0  ...   
3          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
4          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
5          4.0   3.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
939        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   5.0   0.0  ...   
940        0.0   0.0   0.0   2.0   0.0   0.0   4.0   5.0   3.0   0.0  ...   
941        5.0   0.0   0.0   0.0   0.0   0.0   4.0   0.0   0.0   0.0  ...   
942        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
943        0.0   5.0   0.0   0.0   0.0   0.0   0.0   0.0   3.0   0.0  ...   

movie_id  1673  1674  1675  1676  1677  1678  1679  1680  1681  1682  
user_id                                                               
1          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
2          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
3          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
4          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
5          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
939        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
940        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
941        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
942        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
943        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  

[943 rows x 1682 columns]

In [18]:
user_similarity = cosine_similarity(dummy_matrix, dummy_matrix)
user_similarity

array([[1.        , 0.16693098, 0.04745954, ..., 0.14861694, 0.17950788,
        0.39817474],
       [0.16693098, 1.        , 0.11059132, ..., 0.16148478, 0.17226781,
        0.10579788],
       [0.04745954, 0.11059132, 1.        , ..., 0.10124256, 0.13341615,
        0.02655587],
       ...,
       [0.14861694, 0.16148478, 0.10124256, ..., 1.        , 0.1016418 ,
        0.09511958],
       [0.17950788, 0.17226781, 0.13341615, ..., 0.1016418 , 1.        ,
        0.18246466],
       [0.39817474, 0.10579788, 0.02655587, ..., 0.09511958, 0.18246466,
        1.        ]])

In [20]:
user_similarity = pd.DataFrame(user_similarity, index=rating_matrix.index, columns=rating_matrix.index)
user_similarity

user_id       1         2         3         4         5         6         7    \
user_id                                                                         
1        1.000000  0.166931  0.047460  0.064358  0.378475  0.430239  0.440367   
2        0.166931  1.000000  0.110591  0.178121  0.072979  0.245843  0.107328   
3        0.047460  0.110591  1.000000  0.344151  0.021245  0.072415  0.066137   
4        0.064358  0.178121  0.344151  1.000000  0.031804  0.068044  0.091230   
5        0.378475  0.072979  0.021245  0.031804  1.000000  0.237286  0.373600   
...           ...       ...       ...       ...       ...       ...       ...   
939      0.118095  0.228583  0.026271  0.030138  0.071459  0.111852  0.107027   
940      0.314072  0.226790  0.161890  0.196858  0.239955  0.352449  0.329925   
941      0.148617  0.161485  0.101243  0.152041  0.139595  0.144446  0.059993   
942      0.179508  0.172268  0.133416  0.170086  0.152497  0.317328  0.282003   
943      0.398175  0.105798  0.026556  0.058752  0.313941  0.276042  0.394364   

user_id       8         9         10   ...       934       935       936  \
user_id                                ...                                 
1        0.319072  0.078138  0.376544  ...  0.369527  0.119482  0.274876   
2        0.103344  0.161048  0.159862  ...  0.156986  0.307942  0.358789   
3        0.083060  0.061040  0.065151  ...  0.031875  0.042753  0.163829   
4        0.188060  0.101284  0.060859  ...  0.052107  0.036784  0.133115   
5        0.248930  0.056847  0.201427  ...  0.338794  0.080580  0.094924   
...           ...       ...       ...  ...       ...       ...       ...   
939      0.095898  0.039852  0.071460  ...  0.066039  0.431154  0.258021   
940      0.246883  0.120495  0.342961  ...  0.327153  0.107024  0.187536   
941      0.146145  0.143245  0.090305  ...  0.046952  0.203301  0.288318   
942      0.175322  0.092497  0.212330  ...  0.226440  0.073513  0.089588   
943      0.299809  0.075617  0.221860  ...  0.263791  0.210763  0.143253   

user_id       937       938       939       940       941       942       943  
user_id                                                                        
1        0.189705  0.197326  0.118095  0.314072  0.148617  0.179508  0.398175  
2        0.424046  0.319889  0.228583  0.226790  0.161485  0.172268  0.105798  
3        0.069038  0.124245  0.026271  0.161890  0.101243  0.133416  0.026556  
4        0.193471  0.146058  0.030138  0.196858  0.152041  0.170086  0.058752  
5        0.079779  0.148607  0.071459  0.239955  0.139595  0.152497  0.313941  
...           ...       ...       ...       ...       ...       ...       ...  
939      0.226449  0.432666  1.000000  0.087687  0.180029  0.043264  0.144250  
940      0.181317  0.175158  0.087687  1.000000  0.145152  0.261376  0.241028  
941      0.234211  0.313400  0.180029  0.145152  1.000000  0.101642  0.095120  
942      0.129554  0.099385  0.043264  0.261376  0.101642  1.000000  0.182465  
943      0.077793  0.202244  0.144250  0.241028  0.095120  0.182465  1.000000  

[943 rows x 943 columns]

In [21]:
def recommend_movie_knn(user_id, n_items, neighbor_size=30):
    user_movie = rating_matrix.loc[user_id].copy()
    
    for movie in rating_matrix:
        # 이미 사용자가 평가한 영화의 경우 추천 대상에서 제외
        if pd.notnull(user_movie.loc[movie]):
            user_movie.loc[movie] = 0
        
        # 평가하지 않은 영화의 경우 cf_knn으로 예상 평점 계산
        else:
            user_movie.loc[movie] = cf_knn(user_id, movie, neighbor_size)
            
    movie_sort = user_movie.sort_values(ascending=False)[:n_items]
    recommend_movies = movies.loc[movie_sort.index]
    recommendations = recommend_movies['title']
    
    return recommendations

recommend_movie_knn(user_id=2, n_items=5, neighbor_size=30)

movie_id
1293                     Ayn Rand: A Sense of Life (1997)
1189                              That Old Feeling (1997)
1500    Prisoner of the Mountains (Kavkazsky Plennik) ...
1467                                     Cure, The (1995)
318                       Everyone Says I Love You (1996)
Name: title, dtype: object

### Decide optimal neighbor size

In [24]:
rating_matrix = x_train.pivot_table(values='rating', index='user_id', columns='movie_id')
dummy_matrix = rating_matrix.copy().fillna(0)
user_similarity = cosine_similarity(dummy_matrix, dummy_matrix)
user_similarity = pd.DataFrame(user_similarity, index=rating_matrix.index, columns=rating_matrix.index)

for neighbor_size in [10, 20, 30, 40, 50, 60]:
    print("Neighbor size = %d : RMSE = %.4f" % (neighbor_size, score(cf_knn, neighbor_size)))

Neighbor size = 10 : RMSE = 1.0285
Neighbor size = 20 : RMSE = 1.0141
Neighbor size = 30 : RMSE = 1.0116
Neighbor size = 40 : RMSE = 1.0114
Neighbor size = 50 : RMSE = 1.0118
Neighbor size = 60 : RMSE = 1.0122


### CF considering user bias

In [25]:
# rating mean of all user and rating deviation of movies
rating_mean = rating_matrix.mean(axis=1)
rating_bias = (rating_matrix.T - rating_mean).T

def cf_knn_bias(user_id, movie_id, neighbor_size=0):
    if movie_id in rating_bias:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_bias[movie_id].copy() # get rating from user-item matrix
        none_rating_idx = movie_ratings[movie_ratings.isnull()].index # list
        movie_ratings = movie_ratings.drop(none_rating_idx)
        sim_scores = sim_scores.drop(none_rating_idx)
        
        # if neighbor size is not fixed
        if neighbor_size == 0:
            prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum() # weighted average
            prediction = prediction + rating_mean[user_id]
        
        # if neighbor size is fixed
        else:
            if len(sim_scores) > 1:
                neighbor_size = min(neighbor_size, len(sim_scores))
                sim_scores = np.array(sim_scores)
                movie_ratings = np.array(movie_ratings)
                
                user_idx = np.argsort(sim_scores)
                sim_scores = sim_scores[user_idx][-neighbor_size:]
                movie_ratings = movie_ratings[user_idx][-neighbor_size:]
                prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
                prediction = prediction + rating_mean[user_id]
            else:
                prediction = rating_mean[user_id]
        
    else:
        prediction = rating_mean[user_id]
    
    return prediction

score(cf_knn_bias, neighbor_size=30)  

0.9452994907685661

In [ ]:
# practice 3-2 

### Other improving method of CF

In [ ]:
# Significance weighting